In [1]:
import pandas as pd
import numpy as np
import pydicom
import glob
from pathlib import Path
from wsl.locations import wsl_data_dir
import matplotlib.pyplot as plt

In [2]:
def mask2rle(img, width, height):
    rle = []
    lastColor = 0
    currentPixel = 0
    runStart = -1
    runLength = 0

    for x in range(width):
        for y in range(height):
            currentColor = img[x][y]
            if currentColor != lastColor:
                if currentColor == 255:
                    runStart = currentPixel
                    runLength = 1
                else:
                    rle.append(str(runStart))
                    rle.append(str(runLength))
                    runStart = -1
                    runLength = 0
                    currentPixel = 0
            elif runStart > -1:
                runLength += 1
            lastColor = currentColor
            currentPixel+=1

    return " ".join(rle)

In [3]:
def rle2mask(rle, width, height):
    mask= np.zeros(width * height)
    array = np.asarray([int(x) for x in rle.split()])
    starts = array[0::2]
    lengths = array[1::2]

    current_position = 0
    for index, start in enumerate(starts):
        current_position += start
        mask[current_position:current_position+lengths[index]] = 255
        current_position += lengths[index]

    return mask.reshape(width, height)

In [4]:
df = pd.read_csv('original.csv', index_col=0)
#df.columns = ['id', 'EncodedPixels']
df.head()

ImageId  \
420   1.2.276.0.7230010.3.1.4.8323329.3678.151787517...   
9772  1.2.276.0.7230010.3.1.4.8323329.4200.151787518...   
1542  1.2.276.0.7230010.3.1.4.8323329.4862.151787518...   
7532  1.2.276.0.7230010.3.1.4.8323329.12313.15178752...   
5542  1.2.276.0.7230010.3.1.4.8323329.14214.15178752...   

                                          EncodedPixels  
420   194329 37 960 69 919 111 913 117 910 116 912 5...  
9772                                                 -1  
1542  344265 2 1020 7 1015 9 1012 12 1010 14 1008 15...  
7532                                                 -1  
5542                                                 -1

In [5]:
files = glob.glob(str(wsl_data_dir) + '/siim/*/*/*.dcm')
files

['/data/2015P002510/Mehak/git_wsl/data/siim/1.2.276.0.7230010.3.1.2.8323329.11585.1517875233.741598/1.2.276.0.7230010.3.1.3.8323329.11585.1517875233.741597/1.2.276.0.7230010.3.1.4.8323329.11585.1517875233.741599.dcm',
 '/data/2015P002510/Mehak/git_wsl/data/siim/1.2.276.0.7230010.3.1.2.8323329.11586.1517875233.745118/1.2.276.0.7230010.3.1.3.8323329.11586.1517875233.745117/1.2.276.0.7230010.3.1.4.8323329.11586.1517875233.745119.dcm',
 '/data/2015P002510/Mehak/git_wsl/data/siim/1.2.276.0.7230010.3.1.2.8323329.11587.1517875233.749388/1.2.276.0.7230010.3.1.3.8323329.11587.1517875233.749387/1.2.276.0.7230010.3.1.4.8323329.11587.1517875233.749389.dcm',
 '/data/2015P002510/Mehak/git_wsl/data/siim/1.2.276.0.7230010.3.1.2.8323329.11588.1517875233.762990/1.2.276.0.7230010.3.1.3.8323329.11588.1517875233.762989/1.2.276.0.7230010.3.1.4.8323329.11588.1517875233.762991.dcm',
 '/data/2015P002510/Mehak/git_wsl/data/siim/1.2.276.0.7230010.3.1.2.8323329.11589.1517875233.761332/1.2.276.0.7230010.3.1.3.8323

In [6]:
data = {'Id': [],
        'Pneumothorax': [],
        'Rle': []
       }
for file in files:
    ds = pydicom.dcmread(file)
    study = ds.PatientID
    img = ds.pixel_array
    rows, cols = ds.Rows, ds.Columns
    
    # plt.figure(figsize=(8, 8))
    # plt.imshow(img, cmap=plt.cm.bone)
    eps = df[df.ImageId == Path(file).stem].EncodedPixels.to_list()
    print(len(eps), eps)
    mask = np.zeros((cols, rows))
    label = 1
    for ep in eps:
        if ep != '-1':
            mask += rle2mask(ep, cols, rows).T
            # plt.imshow(img + mask, cmap=plt.cm.bone)
        else:
            label = 0
    # plt.show()
    
    parents = file.split('/')
    data['Id'].append(parents[-3] + '/' + parents[-2] + '/' + Path(file).stem)
    data['Pneumothorax'].append(label)
    data['Rle'].append(eps)

1 ['-1']
1 ['-1']
1 ['-1']
1 ['-1']
1 ['-1']
1 ['-1']
1 ['-1']
1 ['-1']
1 ['-1']
1 ['-1']
1 ['-1']
1 ['551119 1 1016 8 1008 15 1002 22 999 25 996 27 995 28 994 30 992 31 991 32 991 33 989 34 988 34 989 33 990 32 990 32 991 32 991 31 991 32 991 31 992 30 992 31 992 30 993 30 993 29 994 29 994 29 994 29 994 29 994 29 995 28 995 28 995 29 995 28 996 27 997 27 996 27 997 27 997 26 998 26 998 25 999 24 1000 24 1000 23 1000 24 1000 23 1001 22 1002 22 1001 22 1002 21 1002 22 1002 21 1003 20 1003 21 1003 20 1004 19 1004 20 1004 19 1005 19 1005 18 1006 18 1006 17 1006 18 1006 17 1007 17 1007 16 1008 16 1008 15 1009 15 1009 15 1009 14 1010 14 1010 13 1011 13 1011 13 1011 12 1012 12 1012 12 1012 11 1013 11 1013 11 1013 10 1014 10 1014 10 1014 9 1015 9 1015 9 1015 8 1016 8 1016 8 1016 8 1016 8 1016 8 1016 7 1017 7 1018 6 1018 6 1018 6 1018 5 1019 5 1020 4 1020 4 1020 4 1020 4 1020 4 1021 3 1021 3 1021 4 1020 4 1020 4 1020 4 1021 3 1021 4 1020 4 1020 4 1020 4 1020 5 1020 4 1020 4 1020 5 1019 5 1019

1 ['605288 3 1021 4 1020 4 1020 5 1019 5 1019 5 1020 5 1019 5 1019 6 1018 6 1018 7 1018 6 1018 7 1017 7 1017 7 1017 8 1017 7 1017 8 1017 7 1017 8 1016 8 1017 8 1016 8 1016 8 1016 9 1015 9 1016 8 1016 8 1017 7 1017 8 1017 7 1017 8 1017 7 1017 8 1016 9 1016 8 1016 9 1016 9 1015 10 1014 11 1014 11 1013 12 1012 13 1011 14 1011 13 1011 14 1011 14 1010 15 1009 15 1010 15 1009 16 1009 16 1008 16 1008 17 1008 16 1008 17 1008 16 1008 17 1008 16 1008 16 1009 15 1009 15 1009 16 1009 15 1009 15 1010 14 1010 14 1011 14 1010 14 1011 14 1010 14 1010 14 1011 14 1011 14 1011 14 1010 14 1011 14 1010 14 1011 14 1010 14 1010 15 1010 15 1009 15 1010 15 1009 15 1010 15 1010 15 1009 16 1009 15 1009 16 1009 15 1009 16 1009 15 1009 16 1009 15 1010 15 1010 14 1010 14 1011 14 1010 15 1010 15 1009 15 1009 16 1009 15 1010 15 1010 14 1010 15 1010 15 1010 15 1010 14 1010 15 1010 15 1010 15 1010 14 1010 15 1010 15 1010 15 1010 15 1009 16 1009 16 1009 16 1009 16 1008 17 1008 17 1008 17 1008 17 1008 17 1008 17 1008 17 

1 ['-1']
1 ['-1']
1 ['-1']
1 ['-1']
1 ['-1']
2 ['257413 10 1006 22 997 33 985 57 961 69 947 78 941 84 933 91 932 92 931 92 930 94 928 95 926 97 925 97 926 98 925 99 923 101 920 103 917 106 917 106 915 109 913 111 912 111 910 114 910 114 911 113 915 110 917 107 920 103 924 100 928 96 931 92 936 88 939 85 942 81 945 78 948 75 952 71 957 67 960 63 964 59 967 56 971 52 976 48 978 45 982 42 984 39 985 39 986 37 987 36 989 34 991 32 992 32 993 30 994 29 996 27 998 25 999 23 1001 22 1003 20 1005 19 1010 12 1015 7 1021 1', '340146 4 1015 11 1006 19 1002 22 997 27 995 29 989 35 987 36 985 39 984 39 983 41 981 42 980 44 978 45 977 47 976 47 975 49 974 49 974 50 973 51 972 51 972 52 971 52 971 53 970 53 970 54 969 54 970 53 970 53 970 53 971 52 971 52 971 52 972 52 971 52 972 51 972 51 973 50 973 50 974 49 974 49 974 49 975 49 974 49 975 48 976 47 978 46 978 45 979 44 980 43 981 43 980 43 980 43 981 42 981 42 981 43 981 42 982 41 983 40 984 39 985 39 984 39 984 39 984 40 983 40 983 40 983 40 983 

1 ['-1']
1 ['-1']
1 ['-1']
1 ['-1']
1 ['-1']
1 ['-1']
1 ['-1']
1 ['-1']
1 ['453982 26 991 38 976 55 953 78 945 82 940 87 936 89 933 93 929 96 926 100 922 103 920 105 917 107 915 110 908 116 890 135 880 144 876 148 872 152 869 155 867 157 865 159 862 162 860 163 859 165 857 166 855 168 853 171 849 174 847 176 845 179 843 180 842 182 840 183 838 185 837 186 836 187 834 189 833 190 832 192 830 193 829 194 828 195 827 195 828 195 827 195 826 196 825 196 825 196 825 196 827 194 828 189 834 184 837 180 842 177 845 177 845 177 846 175 849 171 852 170 854 169 855 166 857 164 860 162 862 159 866 155 876 143 905 104 927 88 943 74 968 50 992 27 1000 20']
1 ['-1']
1 ['570524 8 1006 22 998 27 994 31 990 35 986 38 983 42 980 44 977 47 975 49 973 51 971 53 970 54 968 56 967 57 966 57 965 58 965 59 964 59 963 60 963 58 965 56 966 54 969 53 970 52 972 51 972 50 973 50 973 50 974 49 974 49 974 49 974 49 975 48 975 48 975 48 976 48 975 48 976 47 977 46 977 45 979 44 979 44 980 42 981 42 982 41 982 42 982

1 ['-1']
1 ['299144 5 1018 6 1017 7 1015 9 1013 12 1011 13 1009 15 1008 15 1007 17 1006 18 1005 18 1005 19 1004 19 1004 20 1002 21 1002 21 1001 23 1000 23 1000 23 1000 24 999 24 999 24 999 24 999 25 998 25 998 25 998 25 998 26 997 26 997 26 997 27 996 27 996 28 995 29 994 30 993 30 994 30 993 31 992 32 991 33 990 33 990 34 989 35 989 35 988 36 987 36 987 37 987 37 986 38 985 39 985 38 985 39 985 39 984 40 983 40 984 40 983 41 982 42 982 42 981 42 982 42 981 43 981 43 980 43 980 44 980 44 979 45 979 44 979 45 979 45 978 46 978 45 978 46 978 46 977 47 977 46 977 47 977 47 977 46 977 47 977 47 977 47 976 47 977 47 976 48 976 47 977 47 977 47 977 47 976 47 977 47 977 47 977 47 976 48 976 47 977 47 977 47 977 47 977 47 977 47 977 47 977 46 978 46 978 46 978 46 978 46 978 46 977 46 978 46 978 46 978 45 979 45 979 45 979 45 979 45 979 45 980 44 980 43 981 43 981 43 981 43 981 42 982 42 982 42 982 42 982 42 982 42 982 42 982 42 982 43 982 42 982 42 982 43 981 43 981 43 982 42 982 42 982 42 982

...

1 ['-1']
1 ['-1']
1 ['-1']
1 ['-1']
1 ['-1']
1 ['233780 6 1015 19 1003 26 996 32 990 39 983 51 972 57 965 64 958 71 951 78 943 83 939 88 935 91 931 95 928 97 925 100 922 102 919 106 916 108 915 109 913 111 912 112 910 114 908 116 906 118 905 119 903 121 901 123 899 124 899 125 897 127 896 127 894 130 892 131 892 132 890 133 890 133 890 133 889 134 889 134 889 134 888 134 889 134 889 134 888 134 889 134 889 133 889 133 890 131 892 130 892 131 892 130 893 130 892 129 894 128 895 127 895 127 896 125 898 124 900 123 900 122 901 122 901 121 903 119 904 119 904 118 905 118 906 117 906 118 905 118 906 117 907 116 908 116 907 116 908 115 908 115 908 116 908 115 908 115 908 116 907 116 908 116 907 117 906 117 906 118 906 117 906 118 906 118 907 116 909 115 910 114 911 113 912 112 914 110 916 109 918 106 920 104 922 102 924 100 927 98 928 96 930 94 932 92 936 88 941 84 945 79 949 75 954 70 959 65 964 59 975 48 981 43 991 32 997 25 1014 7 106399 6 1012 15 1006 21 1001 25 997 30 993 33 989 37 986 

1 ['517315 7 1011 14 1005 20 1000 25 978 46 973 51 969 55 967 57 965 59 964 60 963 61 962 62 961 63 960 64 959 65 957 67 955 69 954 70 954 70 953 71 953 71 952 72 951 73 949 75 948 76 947 77 946 78 946 78 945 79 944 80 943 81 943 81 942 82 942 82 941 83 940 83 940 84 940 84 939 85 938 86 937 87 937 87 936 88 936 88 935 89 935 89 934 90 934 90 933 91 933 91 932 92 932 92 931 93 931 93 931 93 930 94 930 94 930 94 930 94 930 94 930 94 930 94 930 93 931 93 931 93 931 93 932 92 932 92 932 92 932 92 932 92 932 92 933 91 933 91 933 91 933 91 933 91 933 91 934 90 934 90 934 90 934 90 934 90 935 89 936 88 936 88 937 87 938 86 939 84 941 83 942 82 943 81 943 81 943 81 944 79 945 79 945 79 946 78 947 77 947 76 949 75 950 74 950 74 951 73 951 73 952 72 952 72 952 72 953 71 953 70 955 69 955 69 955 68 957 67 958 66 958 66 959 65 959 65 960 64 960 64 961 63 961 63 961 63 962 62 963 60 964 60 965 59 965 58 967 57 967 57 968 55 969 55 970 54 970 54 971 53 971 52 973 51 974 50 974 50 975 48 976 48 977 

1 ['281013 1 1020 5 1017 5 1015 7 1011 11 1010 13 1008 14 1005 18 1000 22 996 27 991 32 989 33 982 40 979 40 977 46 973 49 973 49 972 49 970 51 967 52 969 52 970 51 970 52 969 49 972 50 971 52 967 55 966 56 965 58 963 59 962 59 961 61 961 62 960 63 958 65 956 67 955 67 954 68 954 68 954 69 953 69 953 69 953 70 953 69 953 69 954 68 955 67 955 68 955 67 955 67 955 64 959 62 960 61 961 61 962 60 962 60 962 60 963 59 963 60 963 60 962 61 962 61 962 61 962 61 961 62 961 63 959 64 958 65 958 66 957 66 957 67 956 67 955 69 954 69 953 71 952 71 952 72 951 72 951 73 950 73 950 74 950 73 950 74 949 74 950 74 948 75 948 75 949 75 948 75 948 76 948 75 948 76 948 75 948 76 947 77 947 77 946 77 947 77 946 78 946 78 945 79 945 79 944 80 944 80 943 81 942 82 941 83 940 84 940 84 939 85 939 85 938 86 937 87 937 88 935 89 935 89 934 90 933 92 932 92 931 93 930 95 928 96 928 96 927 97 926 98 926 99 924 100 924 100 923 101 923 101 923 101 922 102 922 103 921 103 920 105 919 105 918 106 918 106 917 107 917

1 ['272705 3 1019 3 1018 2 1020 1 1021 1 1019 3 1017 6 1015 7 1015 7 1016 5 1017 5 1018 3 1020 2 1020 2 2041 2 1019 3 1019 3 1019 4 1017 5 1015 7 1014 8 1014 9 1013 9 1013 10 1012 9 1014 8 1014 9 1013 9 1013 10 1013 10 1012 10 1013 10 1012 11 1011 11 1012 11 1012 11 1012 10 1013 10 1013 10 1012 10 1013 10 1013 10 1012 12 1011 12 1011 12 1012 11 1012 10 1013 10 1013 10 1014 10 1013 10 1013 10 1013 10 1014 8 1015 8 1015 8 1015 7 1017 6 1017 6 1017 7 1016 7 1017 6 1017 6 1017 6 1017 6 1017 6 1017 6 1011 1 5 6 1011 1 4 7 1011 2 2 8 1011 2 1 10 1010 13 1011 12 1011 12 1011 12 1011 12 1011 12 1011 12 1010 13 1010 13 1009 14 1009 14 1009 14 1009 14 1009 14 1009 15 1008 15 1008 15 1008 15 1009 15 1008 15 1008 15 1009 15 1008 15 1009 15 1008 15 1009 15 1008 15 1009 15 1009 15 1008 15 1008 16 1008 16 1007 17 1006 17 1007 17 1006 18 1006 18 1006 18 1005 18 1006 18 1006 18 1005 19 1005 19 1005 18 1005 19 1005 19 1005 19 1004 20 1004 19 1004 20 1004 20 1004 20 1003 21 1003 21 1003 21 1003 21 1002 2

1 ['-1']
1 ['-1']
1 ['643446 1 1022 5 1017 8 1015 9 1014 10 1012 12 1011 13 1010 14 1010 14 1009 15 1008 16 1008 16 1007 17 1007 17 1007 17 1006 17 1007 17 1006 18 1006 17 1006 18 1006 18 1005 18 1006 18 1006 18 1005 18 1006 18 1005 19 1005 18 1005 19 1005 19 1005 19 1005 18 1005 19 1005 19 1006 18 1006 18 1006 18 1006 18 1006 18 1007 17 1007 17 1007 16 1008 16 1008 16 1009 15 1009 15 1009 14 1010 14 1010 14 1010 14 1010 14 1010 13 1011 13 1012 11 1015 8']
1 ['-1']
1 ['757984 1 4098 1 1024 2 1022 4 1021 4 1021 4 1021 5 1020 6 1019 8 1017 9 1016 16 1010 15 1010 16 1009 17 1009 16 1009 17 1009 17 1009 16 1009 16 1009 17 1008 17 1008 17 1008 18 1008 17 1009 16 1009 16 1010 15 1011 14 1012 13 1013 12 1014 11 1014 11 1014 10 1016 9 1016 9 1016 9 1016 9 1016 10 1016 9 1017 8 1018 7 1020 6 1019 6 1020 5 1021 5 1021 4 1023 2 1024 1 2050 2 1023 3 1023 3 1023 2 1024 1']
1 ['-1']
1 ['-1']
1 ['400668 3 1016 10 1012 13 1008 17 1005 20 1003 23 1000 24 999 26 997 27 996 28 995 30 993 31 992 34 989 36

In [7]:
info = df.from_dict(data)
display(info)
info.to_csv('info.csv', index=False)

Id  Pneumothorax  \
0      1.2.276.0.7230010.3.1.2.8323329.11585.15178752...             0   
1      1.2.276.0.7230010.3.1.2.8323329.11586.15178752...             0   
2      1.2.276.0.7230010.3.1.2.8323329.11587.15178752...             0   
3      1.2.276.0.7230010.3.1.2.8323329.11588.15178752...             0   
4      1.2.276.0.7230010.3.1.2.8323329.11589.15178752...             0   
...                                                  ...           ...   
10350  1.2.276.0.7230010.3.1.2.8323329.7049.151787520...             0   
10351  1.2.276.0.7230010.3.1.2.8323329.705.1517875164...             1   
10352  1.2.276.0.7230010.3.1.2.8323329.7050.151787520...             0   
10353  1.2.276.0.7230010.3.1.2.8323329.7051.151787520...             0   
10354  1.2.276.0.7230010.3.1.2.8323329.7052.151787520...             0   

                                                     Rle  
0                                                   [-1]  
1                                                   [-1]  
2                                                   [-1]  
3                                                   [-1]  
4                                                   [-1]  
...                                                  ...  
10350                                               [-1]  
10351  [338106 1 1019 4 1017 6 1016 8 1015 8 1014 9 1...  
10352                                               [-1]  
10353                                               [-1]  
10354                                               [-1]  

[10355 rows x 3 columns]

In [8]:
import random
patients = list(set(info['Id'].tolist()))
random.shuffle(patients)
print(len(patients))

splits = {'train':patients[:8284],
          'valid':patients[8284:9320],
          'test':patients[9320:]}

for key, value in splits.items():
    pdf = info[info.Id.isin(value)]
    display(pdf.head())
    pdf = pd.DataFrame(pdf.Id.tolist(), columns=['Id'])
    pdf.to_csv(key + '.csv', index=False)
    display(pdf.head())

10355


Id  Pneumothorax   Rle
2  1.2.276.0.7230010.3.1.2.8323329.11587.15178752...             0  [-1]
3  1.2.276.0.7230010.3.1.2.8323329.11588.15178752...             0  [-1]
4  1.2.276.0.7230010.3.1.2.8323329.11589.15178752...             0  [-1]
5  1.2.276.0.7230010.3.1.2.8323329.1159.151787516...             0  [-1]
6  1.2.276.0.7230010.3.1.2.8323329.11590.15178752...             0  [-1]

Id
0  1.2.276.0.7230010.3.1.2.8323329.11587.15178752...
1  1.2.276.0.7230010.3.1.2.8323329.11588.15178752...
2  1.2.276.0.7230010.3.1.2.8323329.11589.15178752...
3  1.2.276.0.7230010.3.1.2.8323329.1159.151787516...
4  1.2.276.0.7230010.3.1.2.8323329.11590.15178752...

Id  Pneumothorax  \
15  1.2.276.0.7230010.3.1.2.8323329.11599.15178752...             1   
20  1.2.276.0.7230010.3.1.2.8323329.11603.15178752...             0   
59  1.2.276.0.7230010.3.1.2.8323329.11639.15178752...             1   
78  1.2.276.0.7230010.3.1.2.8323329.11656.15178752...             0   
86  1.2.276.0.7230010.3.1.2.8323329.11663.15178752...             0   

                                                  Rle  
15  [295187 12 1008 17 1004 22 1000 26 995 30 992 ...  
20                                               [-1]  
59  [551082 3 1015 10 1011 14 1006 19 1001 24 997 ...  
78                                               [-1]  
86                                               [-1]

Id
0  1.2.276.0.7230010.3.1.2.8323329.11599.15178752...
1  1.2.276.0.7230010.3.1.2.8323329.11603.15178752...
2  1.2.276.0.7230010.3.1.2.8323329.11639.15178752...
3  1.2.276.0.7230010.3.1.2.8323329.11656.15178752...
4  1.2.276.0.7230010.3.1.2.8323329.11663.15178752...

Id  Pneumothorax   Rle
0   1.2.276.0.7230010.3.1.2.8323329.11585.15178752...             0  [-1]
1   1.2.276.0.7230010.3.1.2.8323329.11586.15178752...             0  [-1]
30  1.2.276.0.7230010.3.1.2.8323329.11612.15178752...             0  [-1]
44  1.2.276.0.7230010.3.1.2.8323329.11625.15178752...             0  [-1]
52  1.2.276.0.7230010.3.1.2.8323329.11632.15178752...             0  [-1]

Id
0  1.2.276.0.7230010.3.1.2.8323329.11585.15178752...
1  1.2.276.0.7230010.3.1.2.8323329.11586.15178752...
2  1.2.276.0.7230010.3.1.2.8323329.11612.15178752...
3  1.2.276.0.7230010.3.1.2.8323329.11625.15178752...
4  1.2.276.0.7230010.3.1.2.8323329.11632.15178752...